## Geospatial Data with Folium

Folium is a Python package used for creating interactive maps. Folium visualizations can be exported as HTML files and incorporated into websites.

Tutorial resources
* https://python-visualization.github.io/folium/latest/getting_started.html
* https://realpython.com/python-folium-web-maps-from-data/

To install, if needed:

In [ ]:
!pip install folium

Let's create a basic map:

In [1]:
import folium

m = folium.Map()
m

We can specify start coordinates and a starting zoom level:

In [7]:
m = folium.Map(location=(49.25, -123.12), zoom_start = 11)
m

We can also adjust the map colors. "The Positron basemap by Carto and Stamen is designed to give viewers geospatial context while keeping the visual impact of the basemap minimal so that you can showcase your own data"

In [8]:
m = folium.Map(location=(49.25, -123.12), zoom_start = 11, tiles='Cartodb positron')
m

Once we get a map we like, we can save the output to an HTML file to share online:

In [ ]:
m.save("vancouver.html")

### Adding Markers 

Let's make a map of where the comic books stores are in the United States
* Data -- https://www.kaggle.com/datasets/thedevastator/u-s-comic-book-stores-geolocation

In [2]:
import pandas as pd

df_comics = pd.read_csv('us_comic_book_stores_geocoded.csv')


In [3]:
df_comics.head()

index                 comic_book_store_name           address  \
0      0                Albertville Candy Shop   118 E. Main St.   
1      1  All American Sports Cards and Comics  106 S. Water St.   
2      2               All Star Comics & Cards    58 N. Main St.   
3      3                  Big Hit Sports Cards  6450 Hwy. 90 #L.   
4      4                          Bob's Comics  979 Gadsden Hwy.   

           city state   latitude  longitude  
0   Albertville    AL  34.267369 -86.207686  
1     Tuscumbia    AL  34.732331 -87.705093  
2          Arab    AL  34.317467 -86.495688  
3  Spanish Fort    AL  30.721340 -87.865999  
4    Birmingham    AL  33.586211 -86.661340

In [9]:
# Center of United States latitude and longitude values
latitude = 38.7946
longitude = -95.5348

In [10]:
# create map and display it
us_map = folium.Map(location=[latitude, longitude], zoom_start=4, tiles='Cartodb positron')

us_map

In [11]:
# instantiate a feature group for the stores in the dataframe
stores = folium.map.FeatureGroup()

for lat, lng, in zip(df_comics.latitude, df_comics.longitude):
    stores.add_child(
        folium.vector_layers.CircleMarker(
            [lat, lng],
            radius=5, # define how big you want the circle markers to be
            color='yellow',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )

# add stores to map
us_map.add_child(stores)

If you scroll around, you'll notice that a number of comic book stores are said to be located just off the coast of Africa. This represents missing values in the data set, where latitude and longitude both default to 0. For our purposes, we can just ignore those points (but it would be something you'd want to fix in an actual project):

In [12]:
# create map and display it
us_map = folium.Map(location=[latitude, longitude], zoom_start=4, tiles='Cartodb positron')

stores = folium.map.FeatureGroup()

for lat, lng, in zip(df_comics.latitude, df_comics.longitude):
    if not (lat == 0 and lng == 0):
        stores.add_child(
            folium.vector_layers.CircleMarker(
                [lat, lng],
                radius=5, # define how big you want the circle markers to be
                color='yellow',
                fill=True,
                fill_color='blue',
                fill_opacity=0.6
            )
        )

# add stores to map
us_map.add_child(stores)


We can also focus out map, and just plot comic book stores in a single area like the state of Utah (focusing on the Wasatch Front):

In [13]:
utah_stores = df_comics.loc[df_comics['state'] == 'UT']


utah_map = folium.Map(location=[40.75, -111.8], zoom_start=9, tiles='Cartodb positron')

stores = folium.map.FeatureGroup()

for lat, lng in zip(utah_stores.latitude, utah_stores.longitude):
    if not (lat == 0 and lng == 0):
        stores.add_child(
            folium.vector_layers.CircleMarker(
                [lat, lng],
                radius=5, # define how big you want the circle markers to be
                color='yellow',
                fill=True,
                fill_color='blue',
                fill_opacity=0.6
            )
        )

# add stores to map
utah_map.add_child(stores)


As of right now, these points are not interactive (clicking on them does nothing). One thing we can do is attach markers to each point that will display the store name (we could also add the store's address if wanted). 

In [14]:
utah_map = folium.Map(location=[40.75, -111.8], zoom_start=9, tiles='Cartodb positron')

stores = folium.map.FeatureGroup()

for lat, lng in zip(utah_stores.latitude, utah_stores.longitude):
    if not (lat == 0 and lng == 0):
        stores.add_child(
            folium.vector_layers.CircleMarker(
                [lat, lng],
                radius=5, # define how big you want the circle markers to be
                color='yellow',
                fill=True,
                fill_color='blue',
                fill_opacity=0.6
            )
        )

# add pop-up text to each marker on the map
latitudes = list(utah_stores.latitude)
longitudes = list(utah_stores.longitude)
labels = list(utah_stores.comic_book_store_name)

for lat, lng, label in zip(latitudes, longitudes, labels):
    folium.Marker([lat, lng], popup=label).add_to(utah_map)    
    
# add stores to map
utah_map.add_child(stores)

The combination of markers and dots is a little cluttered, so we can add the labels directly to the dots using the `popup` attribute:

In [15]:
utah_map = folium.Map(location=[40.75, -111.8], zoom_start=9, tiles='Cartodb positron')

stores = folium.map.FeatureGroup()

for lat, lng, label in zip(utah_stores.latitude, utah_stores.longitude, utah_stores.comic_book_store_name):
    if not (lat == 0 and lng == 0):
        stores.add_child(
            folium.vector_layers.CircleMarker(
                [lat, lng],
                radius=5, # define how big you want the circle markers to be
                color='yellow',
                fill=True,
                fill_color='blue',
                fill_opacity=0.6,
                popup=label
            )
        )
    
# add stores to map
utah_map.add_child(stores)

Notice also that some of the dots are overlapping. This is okay when we zoom in, but it can be hard to tell how many stores there are in an area when we're zoomed out. So we can join all points to a `MarkerCluster` object that will automatically group points that are close together until we zoom in:

In [16]:
from folium import plugins

utah_map = folium.Map(location=[40.75, -111.8], zoom_start=9, tiles='Cartodb positron')

# instantiate a mark cluster object for the incidents in the dataframe
stores = plugins.MarkerCluster().add_to(utah_map)

# loop through the dataframe and add each data point to the mark cluster
for lat, lng, label in zip(utah_stores.latitude, utah_stores.longitude, utah_stores.comic_book_store_name):
    folium.Marker(
        location=[lat, lng],
        icon=None,
        popup=label,
    ).add_to(stores)

# display map
utah_map

### Creating a Choropleth Chart

A <b>choropleth</b> map is like a heat map, but attached to an actual geographical map. Let's use the same comic book store data set to see which states have the most stores:
* We will import state boundaries using GeoJSON

In [17]:
df_comics.head()

index                 comic_book_store_name           address  \
0      0                Albertville Candy Shop   118 E. Main St.   
1      1  All American Sports Cards and Comics  106 S. Water St.   
2      2               All Star Comics & Cards    58 N. Main St.   
3      3                  Big Hit Sports Cards  6450 Hwy. 90 #L.   
4      4                          Bob's Comics  979 Gadsden Hwy.   

           city state   latitude  longitude  
0   Albertville    AL  34.267369 -86.207686  
1     Tuscumbia    AL  34.732331 -87.705093  
2          Arab    AL  34.317467 -86.495688  
3  Spanish Fort    AL  30.721340 -87.865999  
4    Birmingham    AL  33.586211 -86.661340

In [18]:
# Get number of comic stores per state 

state_counts = df_comics["state"].value_counts()
counts_df = pd.DataFrame({"state" : list(state_counts.keys()), "count" : list(state_counts)})
counts_df.head()

state  count
0    CA    203
1    NY    167
2    TX    139
3    OH    130
4    IL    125

In [19]:
import requests

state_geo = requests.get(
    "https://raw.githubusercontent.com/python-visualization/folium-example-data/main/us_states.json"
).json()

m = folium.Map(location=[48, -102], zoom_start=3)

folium.Choropleth(
    geo_data=state_geo,
    name="choropleth",
    data=counts_df,
    columns=["state", "count"],
    key_on="feature.id", # comes from the JSON file
    fill_color="Blues",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Comic Store Count",
).add_to(m)

folium.LayerControl().add_to(m)

m

### County View

If we want to get a more fine-grained view, by county instead of state, we will first need to determine the counties of each store. Let's go back to the Utah stores:

In [20]:
utah_stores.head(20)

index          comic_book_store_name  \
2013   2013               Black Cat Comics   
2014   2014              Comics Plus, Inc.   
2015   2015    Dr. Volts Comics Connection   
2016   2016  Dragon's Keep Comic and Games   
2017   2017          Edgemont Sports Cards   
2018   2018                       End Zone   
2019   2019                  Fantasy Rules   
2020   2020                     Game Haven   
2021   2021               Game Night Games   
2022   2022                 Hastur Hobbies   
2023   2023                  Heebeegeebeez   
2024   2024                  Heebeegeebeez   
2025   2025                   Night Flight   
2026   2026                   Night Flight   

                                            address            city state  \
2013  2263 S. Highland Dr. (The Sugar House Center)  Salt Lake City    UT   
2014                           1812 W. Sunset Blvd.      St. George    UT   
2015                                2023 E. 3300 S.  Salt Lake City    UT   
2016                         260 N. University Ave.           Provo    UT   
2017                               355 S. State St.            Orem    UT   
2018                                133 S State St.      Clearfield    UT   
2019                                 79 S. Main St.  Pleasant Grove    UT   
2020                                1609 W. 9000 S.     West Jordan    UT   
2021                         2030 South 900 East #E  Salt Lake City    UT   
2022                              6831 S. State St.         Midvale    UT   
2023                          2574 Washington Blvd.           Ogden    UT   
2024                      1986 N. Hill Field Rd. #2          Layton    UT   
2025         210 East 400 South #7 (Liberty Square)  Salt Lake City    UT   
2026                              6222 S. State St.  Salt Lake City    UT   

       latitude   longitude  
2013  40.721843 -111.858299  
2014  37.124159 -113.622139  
2015  40.699961 -111.833375  
2016  40.237188 -111.658406  
2017  40.290617 -111.691459  
2018  41.112305 -112.023217  
2019  40.362764 -111.740627  
2020  40.587674 -111.936407  
2021  40.726020 -111.865976  
2022  40.627381 -111.889458  
2023  41.219090 -111.970430  
2024  41.088671 -111.973114  
2025  40.760057 -111.884918  
2026  40.635638 -111.889360

We can import a different GeoJSON file to view comic book store concentration by county instead of state. 

In [21]:
county_geo = requests.get(
    "https://gist.github.com/sdwfrost/d1c73f91dd9d175998ed166eb216994a/raw/e89c35f308cee7e2e5a784e1d3afc5d449e9e4bb/counties.geojson"
).json()

utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles='Cartodb positron')

folium.GeoJson(county_geo, name="hello world").add_to(utah_map)


utah_map


Using a tool like https://mapshaper.org/ we can eliminate unneeded counties and just focus on a particular region (like Utah):

In [22]:
import json

with open("utah_counties.json","r") as f:
    county_geo = json.load(f)

utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles='Cartodb positron')

folium.GeoJson(county_geo, name="hello world").add_to(utah_map)


utah_map


We can use our knowledge of the state of Utah (there aren't too many stores to classify), or an online tool to determine county by the given city and state. (We could also play around with the GPS coordinates if we wanted).

In [ ]:
!pip install geopy

In [23]:
from geopy.geocoders import Nominatim

def get_county(city_name, state_name):
    geolocator = Nominatim(user_agent="county_finder")
    location = geolocator.geocode(f"{city_name}, {state_name}")
    
    vals = str(location).split(",")
    for v in vals:
        if "County" in v:
            return v[:-7].strip() # slice off county   
        
counties = []        
for i in range(len(utah_stores)):
    cur_city = utah_stores["city"].iloc[i]
    counties.append(get_county(cur_city, "UT"))
    
utah_stores["county"] = counties

C:\Users\10502190\AppData\Local\Temp\ipykernel_26620\3183881880.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  utah_stores["county"] = counties


In [24]:
utah_stores.head(20)

index          comic_book_store_name  \
2013   2013               Black Cat Comics   
2014   2014              Comics Plus, Inc.   
2015   2015    Dr. Volts Comics Connection   
2016   2016  Dragon's Keep Comic and Games   
2017   2017          Edgemont Sports Cards   
2018   2018                       End Zone   
2019   2019                  Fantasy Rules   
2020   2020                     Game Haven   
2021   2021               Game Night Games   
2022   2022                 Hastur Hobbies   
2023   2023                  Heebeegeebeez   
2024   2024                  Heebeegeebeez   
2025   2025                   Night Flight   
2026   2026                   Night Flight   

                                            address            city state  \
2013  2263 S. Highland Dr. (The Sugar House Center)  Salt Lake City    UT   
2014                           1812 W. Sunset Blvd.      St. George    UT   
2015                                2023 E. 3300 S.  Salt Lake City    UT   
2016                         260 N. University Ave.           Provo    UT   
2017                               355 S. State St.            Orem    UT   
2018                                133 S State St.      Clearfield    UT   
2019                                 79 S. Main St.  Pleasant Grove    UT   
2020                                1609 W. 9000 S.     West Jordan    UT   
2021                         2030 South 900 East #E  Salt Lake City    UT   
2022                              6831 S. State St.         Midvale    UT   
2023                          2574 Washington Blvd.           Ogden    UT   
2024                      1986 N. Hill Field Rd. #2          Layton    UT   
2025         210 East 400 South #7 (Liberty Square)  Salt Lake City    UT   
2026                              6222 S. State St.  Salt Lake City    UT   

       latitude   longitude      county  
2013  40.721843 -111.858299   Salt Lake  
2014  37.124159 -113.622139  Washington  
2015  40.699961 -111.833375   Salt Lake  
2016  40.237188 -111.658406        Utah  
2017  40.290617 -111.691459        Utah  
2018  41.112305 -112.023217       Davis  
2019  40.362764 -111.740627        Utah  
2020  40.587674 -111.936407   Salt Lake  
2021  40.726020 -111.865976   Salt Lake  
2022  40.627381 -111.889458   Salt Lake  
2023  41.219090 -111.970430       Weber  
2024  41.088671 -111.973114       Davis  
2025  40.760057 -111.884918   Salt Lake  
2026  40.635638 -111.889360   Salt Lake

In [25]:
# Get number of comic stores per state 

county_counts = utah_stores["county"].value_counts()
counts_df = pd.DataFrame({"county" : list(county_counts.keys()), "count" : list(county_counts)})
counts_df.head()

county  count
0   Salt Lake      7
1        Utah      3
2       Davis      2
3  Washington      1
4       Weber      1

To see what property of the JSON file the county name is stored under, we can print it out:

In [26]:
county_geo

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-110.000711, 40.813677999066584],
      [-110.137819, 40.8109129990666],
      [-110.292692, 40.8333429990665],
      [-110.378962, 40.78717999906671],
      [-110.561377, 40.758364999066856],
      [-110.625737, 40.76947099906679],
      [-110.656482, 40.74027499906694],
      [-110.750733, 40.74770599906691],
      [-110.822478, 40.71046099906708],
      [-110.89198, 40.727122999067],
      [-110.901974, 40.67816199906724],
      [-110.891655, 39.899653999071404],
      [-110.857647, 39.899706999071405],
      [-110.85778, 39.813284999071904],
      [-109.976814, 39.806229999071945],
      [-109.976402, 40.8096859990666],
      [-110.000711, 40.813677999066584]]]},
   'properties': {'STATEFP': '49',
    'COUNTYFP': '013',
    'COUNTYNS': '01448021',
    'AFFGEOID': '0500000US49013',
    'GEOID': '49013',
    'NAME': 'Duchesne',
    'LSAD': '06',
    'ALAND': 837950

In [27]:
print(county_geo["features"][0]["properties"]["NAME"])

Duchesne


Now we will make a Utah choropleth map (fingers crossed!):

In [28]:
utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles='Cartodb positron')

folium.Choropleth(
    geo_data=county_geo,
    name="choropleth",
    data=counts_df,
    columns=["county", "count"],
    key_on="feature.properties.NAME",
    fill_color="Blues",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Comic Store Count",
).add_to(utah_map)

folium.LayerControl().add_to(utah_map)

utah_map

In order to get rid of the dark shaded areas where no comic stores are listed, we will add those counties to our data frame with a count of 0:

In [29]:
counties_list = [county_geo["features"][i]["properties"]["NAME"] for i in range(len(county_geo["features"]))]
print(counties_list)
new_counts = []
for c in counties_list:
    if c in county_counts:
        new_counts.append(county_counts[c])
    else:
        new_counts.append(0)

        
counts_df = pd.DataFrame({"county" : counties_list, "count" : new_counts})
counts_df.head(30)    


['Duchesne', 'Cache', 'Sevier', 'Millard', 'Salt Lake', 'Daggett', 'Wayne', 'Weber', 'Juab', 'Garfield', 'Utah', 'San Juan', 'Box Elder', 'Emery', 'Tooele', 'Morgan', 'Uintah', 'Kane', 'Summit', 'Rich', 'Wasatch', 'Carbon', 'Grand', 'Washington', 'Davis', 'Beaver', 'Sanpete', 'Piute', 'Iron']


county  count
0     Duchesne      0
1        Cache      0
2       Sevier      0
3      Millard      0
4    Salt Lake      7
5      Daggett      0
6        Wayne      0
7        Weber      1
8         Juab      0
9     Garfield      0
10        Utah      3
11    San Juan      0
12   Box Elder      0
13       Emery      0
14      Tooele      0
15      Morgan      0
16      Uintah      0
17        Kane      0
18      Summit      0
19        Rich      0
20     Wasatch      0
21      Carbon      0
22       Grand      0
23  Washington      1
24       Davis      2
25      Beaver      0
26     Sanpete      0
27       Piute      0
28        Iron      0

In [30]:
utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles='Cartodb positron')

folium.Choropleth(
    geo_data=county_geo,
    name="choropleth",
    data=counts_df,
    columns=["county", "count"],
    key_on="feature.properties.NAME",
    fill_color="Blues",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Comic Store Count",
).add_to(utah_map)

folium.LayerControl().add_to(utah_map)

utah_map

Add bins to distinguish counties with 1 store vs counties with 0 stores:

In [31]:
utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles='Cartodb positron')

folium.Choropleth(
    geo_data=county_geo,
    name="choropleth",
    data=counts_df,
    columns=["county", "count"],
    key_on="feature.properties.NAME",
    bins = list(range(8)),
    fill_color="Blues",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Comic Store Count",
).add_to(utah_map)

folium.LayerControl().add_to(utah_map)

utah_map

Finally, we can switch off the background and all map controls to just focus on Utah:

In [32]:
utah_map = folium.Map(location=[39.5, -111.8], zoom_start=6, tiles=None, zoom_control=False) # , scrollWheelZoom=False, dragging=False)

folium.Choropleth(
    geo_data=county_geo,
    name="choropleth",
    data=counts_df,
    columns=["county", "count"],
    key_on="feature.properties.NAME",
    bins = list(range(8)),
    fill_color="Blues",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Comic Store Count",
).add_to(utah_map)

utah_map

### Folium "Heat Maps"

Another feature availbe on folium is the "heat source" map:
* See  https://geopandas.org/en/stable/gallery/plotting_with_folium.html

In [6]:
from folium import plugins

latitude = 38.7946
longitude = -95.5348

m = folium.Map(location=[latitude, longitude], tiles="Cartodb dark_matter", zoom_start=4)

heat_data = list(zip(df_comics.latitude, df_comics.longitude))

heat_data
plugins.HeatMap(heat_data).add_to(m)

m